#### Use dependency parsing 
1. to get the number of complex questions
2. to fetch verb-object pairs from raw and NERed sentences 

In [1]:
import json
import pprint
import re
import spacy

In [2]:
with open('data/utterances.json', 'r') as file:
    utter = json.load(file)

print(len(utter))

45797


In [4]:
# data cleaning - get the number of requests without payload
def data_clean():
    num_ureq = 0 
    clean_text = []
    for id in utter:
        for req in utter[id]:
            if req != 'start' and 'feedback' not in req:
                num_ureq += 1
                orig = req
                req = re.sub(r'http://dbpedia.org/resource/', ' ', req)
                req = re.sub(r"-|_|/|!|>|\\", ' ', req) 
                req = re.sub(r"^'", '', req)
                req = re.sub(r' +', ' ', req)
                req = re.sub(r'[t|T][e|E][l|L][l|L] [m|M][e|E] ', 'give ', req)
                if len(req.strip()) > 0:
                    clean_text.append(req)
            
    print('# requests excluding feedback and start payload', num_ureq)
    return clean_text

preprocessed_text = data_clean()
print('# non-blank requests',len(preprocessed_text))

# requests excluding feedback and start payload 30263
# non-blank requests 30253


In [11]:
print(preprocessed_text[:100])

['Who is George MacDonald Church ?', 'Who is Macron ?', 'Who is Emmanuel Macron ?', 'Who is Einstein ?', 'entity information Albert Einstein', 'WHER IS PARIS ?', 'WHERE IS PARIS?', 'WHO IS GEORGE CHURCH?', 'WHO IS MACRON?', "Who is Yao Ming'swife？", 'entity information Albert Einstein', 'entity information Planet', 'get location Berlin', 'dbpedia about', 'entity information Albert Einstein', 'learn more Albert Einstein Albert Einstein', 'load similar Albert Einstein Albert Einstein', 'get location Berlin', 'entity information Planet', 'entity information Berlin', 'learn more Planet Planet', 'load similar Planet Planet', 'load related Planet Planet', 'dbpedia about', 'entity information Albert Einstein', 'get location Berlin', 'learn more Albert Einstein Albert Einstein', 'who is obama', 'get location Berlin', 'where is newyork', 'Where is Beijing', 'Where is Hawaii', 'What is lenovo', 'What is Lenovo', 'entity information Planet', 'get location Berlin', 'Who directed Edge of Tomorrow?'

In [63]:
import ast
with open('data/ner_requests.txt', 'r') as f:
    lines = f.read()
    lines = [line.lower() for line in ast.literal_eval(lines) if len(line) > 0]
    
print(len(lines))

10909


In [2]:
import stanfordnlp
from spacy_stanfordnlp import StanfordNLPLanguage

snlp = stanfordnlp.Pipeline(lang="en")
nlp = StanfordNLPLanguage(snlp)

Use device: cpu
---
Loading: tokenize
With settings: 
{'model_path': '/home/rrichajalota/stanfordnlp_resources/en_ewt_models/en_ewt_tokenizer.pt', 'lang': 'en', 'shorthand': 'en_ewt', 'mode': 'predict'}
---
Loading: pos
With settings: 
{'model_path': '/home/rrichajalota/stanfordnlp_resources/en_ewt_models/en_ewt_tagger.pt', 'pretrain_path': '/home/rrichajalota/stanfordnlp_resources/en_ewt_models/en_ewt.pretrain.pt', 'lang': 'en', 'shorthand': 'en_ewt', 'mode': 'predict'}
---
Loading: lemma
With settings: 
{'model_path': '/home/rrichajalota/stanfordnlp_resources/en_ewt_models/en_ewt_lemmatizer.pt', 'lang': 'en', 'shorthand': 'en_ewt', 'mode': 'predict'}
Building an attentional Seq2Seq model...
Using a Bi-LSTM encoder
Using soft attention for LSTM.
Finetune all embeddings.
[Running seq2seq lemmatizer with edit classifier]
---
Loading: depparse
With settings: 
{'model_path': '/home/rrichajalota/stanfordnlp_resources/en_ewt_models/en_ewt_parser.pt', 'pretrain_path': '/home/rrichajalota/sta

###### no. of complex questions 

In [8]:
def get_complexity(all_text):
    neither = set()
    intj = []
    obl_nn = []
    nsubj_vb = []
    obj_vb=[]
    for text in all_text:
        if text.startswith('load') or text.startswith('learn') or text.startswith('entity'):
            continue
        
        if len(text.split()) > 0:
            doc=nlp(text)
            num_pron_nn = 0
            for token in doc:
                print(token.text, token.dep_, token.pos_, token.head.text, token.head.pos_,  [child for child in token.children])
#                 if token.dep_=='INTJ': # for banter
#                     intj.append(text)
#                     break
                if token.dep_=='obl' and token.pos_=='NOUN' and token.head.pos_=='VERB':
                    print(text)
                    for child in token.children:
                        if child.dep_=='amod' or child.dep_=='nmod':
                            obl_nn.append((text, token.text, child.text))
                            break
                if token.dep_=='nsubj' and token.head.pos_=='VERB':
                    print(text)
                    for child in token.children:
                        if child.dep_=='acl':
                            nsubj_vb.append((text, token.text, child.text))
                            break
                if token.dep_=='obj' and token.head.pos_=='VERB':
                    for child in token.children:
                        if child.dep_=='amod' or child.dep_=='nummod':
                            obj_vb.append((text, token.text, child.text))
                            break
                else:
                    neither.add(text)

    return neither, obl_nn, nsubj_vb, obj_vb
neither, obl_nn, nsubj_vb,obj_vb = get_complexity(preprocessed_text) # ["who scored max touchdowns ever"]
# neither, obl_nn, nsubj_vb,obj_vb = get_complexity(['what movies are playing right now '])

what det DET movies NOUN []
movies nsubj NOUN playing VERB [what]
what movies are playing right now 
are aux AUX playing VERB []
playing root VERB playing VERB [movies, are, now]
right advmod ADV now ADV []
now advmod ADV playing VERB [right]


/pytorch/aten/src/ATen/native/LegacyDefinitions.cpp:14: UserWarning: masked_fill_ received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.


In [9]:
print(len(obl_nn))

0


In [10]:
print(len(nsubj_vb))

0


In [11]:
print(obj_vb)

[]


In [12]:
print(neither)

{'what movies are playing right now '}


###### dependency parsing - input data for clustering (using stanfordNLP)

In [32]:
import stanfordnlp
from spacy_stanfordnlp import StanfordNLPLanguage

def get_vo_dependency(all_text):
    vb_obj = [] 
    vo = []
    case_nmod =  []
    nsubj_nn =  []
    nmod_nn =  []
    cop_nn =  []
    nmod_prop =  []
    
    snlp = stanfordnlp.Pipeline(lang="en")
    nlp = StanfordNLPLanguage(snlp)

    for text in all_text:
#         print(text)
        if len(text) > 0:
            doc = nlp(text)
            for token in doc:
                #if token.dep_ == 'nmod' and token.head.pos_ == 'PROPN':
#                 print(token.text, token.dep_, token.pos_, token.head.text, token.head.pos_,  [child for child in token.children])
#         break
            has_vo = False
            has_cop_nn = False
            has_nmod_nn = False
            has_nsubj_nn = False
            has_nmod_ppn = False
            has_case_nmod = False
            if any(token.dep_=='obj' and token.head.pos_ == 'VERB' for token in doc):
                for token in doc:
                    if token.dep_ == 'obj' and token.head.pos_ == 'VERB':
                        print(f'vb_obj: {text}')
                        vb_obj.append((token.head.text, token.text))
                        vo.append((text, token.head.text, token.text))
                        has_vo = True
                        break
            elif not has_vo and any(token.dep_ == 'nmod' and token.head.pos_ == 'NOUN' for token in doc):
                for token in doc:
                    if token.dep_ == 'nmod' and token.head.pos_ == 'NOUN':#
                        print(f'nmod_nn: {text}')
                        vb_obj.append((token.head.text, token.text))
                        has_nmod_nn = True
                        nmod_nn.append((text, token.head.text, token.text))
                        break
            elif not has_nmod_nn and any(token.dep_ == 'nsubj' and (token.head.pos_ == 'NOUN' or token.head.pos_ == 'PRON')
                                        for token in doc):
                for token in doc:
                    if token.dep_ == 'nsubj' and (token.head.pos_ == 'NOUN' or token.head.pos_ == 'PRON'):
                        print(f'nsubj_nn: {text}')
                        vb_obj.append((token.head.text, token.text))
                        has_nsubj_nn = True
                        nsubj_nn.append((text, token.head.text, token.text))
                        break
            elif not has_nsubj_nn and any(token.dep_ == 'nmod' and token.head.pos_ == 'PROPN' for token in doc):
                for token in doc:
                    if token.dep_ == 'nmod' and token.head.pos_ == 'PROPN':
                        print(f'nmod_prop: {text}')
                        vb_obj.append((token.head.text, token.text))
                        nmod_prop.append((text, token.head.text, token.text))
                        has_nmod_ppn = True
                        break
            elif not has_nmod_ppn:
                for token in doc:
                    if token.dep_ == 'case' and token.head.dep_ == 'nmod':
                        print(f'case_nmod: {text}')
                        vb_obj.append((token.text, token.head.text))
                        case_nmod.append((text, token.head.text, token.text))
                        has_case_nmod = True
                        break
            elif not has_case_nmod and any(token.dep_ == 'cop' and token.head.pos_ == 'NOUN' for token in doc):
                for token in doc:                    
                    if token.dep_ == 'cop' and token.head.pos_ == 'NOUN':
                        print(f'cop_nn: {text}')
                        vb_obj.append((token.head.text, token.text))
                        has_cop_nn = True 
                        cop_nn.append((text, token.head.text, token.text))
                        break
            else:
                print('no case: ', text)
                for token in doc:
                    print(token.text, token.dep_, token.pos_, token.head.text, token.head.pos_,  [child for child in token.children])
               
            print(token.text, token.dep_, token.pos_, token.head.text, token.head.pos_,  [child for child in token.children])
    print(vb_obj)
    print(f'case_nmod: {case_nmod}')
    print(f'nsubj_nn: {nsubj_nn}')
    print(f'nmod_nn: {nmod_nn}')
    print(f'cop_nn: {cop_nn}')
    print(f'nmod_prop: {nmod_prop}')
    return vb_obj, vo, case_nmod, nsubj_nn, nmod_nn, cop_nn, nmod_prop   
            
vb_obj, case_nmod, nsubj_nn, nmod_nn, cop_nn, nmod_prop = get_vo_dependency(['Can you give me the names of women born in the Country during the 19th century?', 'How many airports are there in Sofia?', 'is there a tintoretto artworks showing a girl?'])

Use device: cpu
---
Loading: tokenize
With settings: 
{'model_path': '/home/rrichajalota/stanfordnlp_resources/en_ewt_models/en_ewt_tokenizer.pt', 'lang': 'en', 'shorthand': 'en_ewt', 'mode': 'predict'}
---
Loading: pos
With settings: 
{'model_path': '/home/rrichajalota/stanfordnlp_resources/en_ewt_models/en_ewt_tagger.pt', 'pretrain_path': '/home/rrichajalota/stanfordnlp_resources/en_ewt_models/en_ewt.pretrain.pt', 'lang': 'en', 'shorthand': 'en_ewt', 'mode': 'predict'}
---
Loading: lemma
With settings: 
{'model_path': '/home/rrichajalota/stanfordnlp_resources/en_ewt_models/en_ewt_lemmatizer.pt', 'lang': 'en', 'shorthand': 'en_ewt', 'mode': 'predict'}
Building an attentional Seq2Seq model...
Using a Bi-LSTM encoder
Using soft attention for LSTM.
Finetune all embeddings.
[Running seq2seq lemmatizer with edit classifier]
---
Loading: depparse
With settings: 
{'model_path': '/home/rrichajalota/stanfordnlp_resources/en_ewt_models/en_ewt_parser.pt', 'pretrain_path': '/home/rrichajalota/sta

/pytorch/aten/src/ATen/native/LegacyDefinitions.cpp:14: UserWarning: masked_fill_ received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/LegacyDefinitions.cpp:14: UserWarning: masked_fill_ received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/LegacyDefinitions.cpp:14: UserWarning: masked_fill_ received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.


ValueError: too many values to unpack (expected 6)

In [107]:
# save vb-obj pairs for orginal text w/o recognised entities 
print(vb_obj)
# write to file 
with open('data/vb_obj_raw.txt', 'w') as f: 
    f.write(str(vb_obj))

[('Who', 'George'), ('Who', 'Macron'), ('Who', 'Emmanuel'), ('Who', 'Einstein'), ('WHER', 'PARIS'), ('WHO', 'GEORGE'), ('WHO', 'MACRON'), ('get', 'location'), ('dbpedia', 'about'), ('learn', 'Albert'), ('load', 'Albert'), ('get', 'location'), ('learn', 'Planet'), ('load', 'Planet'), ('dbpedia', 'about'), ('get', 'location'), ('learn', 'Albert'), ('get', 'location'), ('get', 'location'), ('directed', 'Edge'), ('plot', 'Titanic'), ('dbpedia', 'about'), ('who', 'sachin'), ('do', 'what'), ('anthem', 'india'), ('birthdate', 'Albert'), ('who', 'sachin'), ('learn', 'Albert'), ('load', 'Albert'), ('founder', 'car'), ('created', 'you'), ('what', 'life'), ('what', 'life'), ('what', 'drawbacks'), ('have', 'bones'), ('name', 'cat'), ('get', 'old'), ('Who', 'Lula'), ('care', 'newborn'), ('have', 'disease'), ('drugs', 'Fever'), ('dbpedia', 'about'), ('get', 'location'), ('who', 'Angela'), ('today', 'is'), ('who', 'you'), ('capital', 'china'), ('dbpedia', 'about'), ('about', 'Rachmaninov'), ('get', '

In [3]:
# vectorize vb-obj pair using spacy vectors for clustering

def prepare_input_rep(vb_obj):
    import spacy
    nlp = spacy.load("/tmp/la_vectors_wiki_lg") # fasttext subword vectors

    vo_rep = []
    lab_vec_map = {}

    for i, pair in enumerate(vb_obj):
        print(i)
        doc = nlp((' '.join(pair)).lower())
        print(doc.text)
        vo_rep.append(doc.vector) # add avg vector
        lab_vec_map[str(doc.vector)] = doc.text
        #print(lab_vec_map[str(doc.vector)])
        #break 
    return vo_rep, lab_vec_map

# vo_rep, lab_vec_map = prepare_input_rep()

In [22]:
# run the pipeline on ner-ed data
import ast, pickle, re

with open('ner_reqs_all.txt', 'r') as f: # ner_requests.txt  unanswered_ner_reqs.txt
    lines = f.read()
    lines = [line for line in ast.literal_eval(lines) if len(line) > 0]
    print(len(lines))
    mlines = []
    for line in lines:
        line = re.sub(r'[t|T][e|E][l|L][l|L] [m|M][e|E] ', 'give ', line)
        mlines.append(line)
    
    print('after modification!!: ', len(mlines))
    gen_vo_pair, vo, case_nmod, nsubj_nn, nmod_nn, cop_nn, nmod_prop = get_vo_dependency(mlines)
#    print(gen_vo_pair)
#     print('CASE_NMOD!!!: ',case_nmod)
#     print('NSUBJ_NN!!!: ',nsubj_nn)
#     print('NMOD_NN!!!: ',nmod_nn)
#     print('COP_NN!!!: ',cop_nn)
#     print('NMOD_PROP!!!: ',nmod_prop)
    vo_rep, lab_vec_map = prepare_input_rep(gen_vo_pair)
    
    print('vec len: ',len(vo_rep))
    
    with open('data/vb_obj_ftext_allSpotlight_ner.pkl', 'wb') as fl:
        pickle.dump(vo_rep, fl)

    with open('data/vb_obj_ner_allSpotlight_ftextLabels.pkl', 'wb') as fl:
        pickle.dump(lab_vec_map, fl)
    
    print('done pickling.!')

27143
after modification!!:  27143
Use device: cpu
---
Loading: tokenize
With settings: 
{'model_path': '/home/rrichajalota/stanfordnlp_resources/en_ewt_models/en_ewt_tokenizer.pt', 'lang': 'en', 'shorthand': 'en_ewt', 'mode': 'predict'}
---
Loading: pos
With settings: 
{'model_path': '/home/rrichajalota/stanfordnlp_resources/en_ewt_models/en_ewt_tagger.pt', 'pretrain_path': '/home/rrichajalota/stanfordnlp_resources/en_ewt_models/en_ewt.pretrain.pt', 'lang': 'en', 'shorthand': 'en_ewt', 'mode': 'predict'}
---
Loading: lemma
With settings: 
{'model_path': '/home/rrichajalota/stanfordnlp_resources/en_ewt_models/en_ewt_lemmatizer.pt', 'lang': 'en', 'shorthand': 'en_ewt', 'mode': 'predict'}
Building an attentional Seq2Seq model...
Using a Bi-LSTM encoder
Using soft attention for LSTM.
Finetune all embeddings.
[Running seq2seq lemmatizer with edit classifier]
---
Loading: depparse
With settings: 
{'model_path': '/home/rrichajalota/stanfordnlp_resources/en_ewt_models/en_ewt_parser.pt', 'pret

/pytorch/aten/src/ATen/native/LegacyDefinitions.cpp:14: UserWarning: masked_fill_ received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/LegacyDefinitions.cpp:14: UserWarning: masked_fill_ received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/LegacyDefinitions.cpp:14: UserWarning: masked_fill_ received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/LegacyDefinitions.cpp:14: UserWarning: masked_fill_ received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.


nsubj_nn: Who is Person ?
nsubj_nn: Who is Person ?
nsubj_nn: Who is Person ?


/pytorch/aten/src/ATen/native/LegacyDefinitions.cpp:14: UserWarning: masked_fill_ received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/LegacyDefinitions.cpp:14: UserWarning: masked_fill_ received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/LegacyDefinitions.cpp:14: UserWarning: masked_fill_ received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/LegacyDefinitions.cpp:14: UserWarning: masked_fill_ received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.


nsubj_nn: WHO IS Person?
nsubj_nn: WHO IS MACRON?
nsubj_nn: Who is Person'swife？


...

11619
open browser
11620
get city
11621
what organization
11622
what organization
11623
perform queries
11624
capital country
11625
president country
11626
founder organization
11627
who giovanni
11628
person who
11629
who ernst
11630
person who
11631
what dildo
11632
what name
11633
whats job
11634
need help
11635
images breakfast
11636
learn planet
11637
have brain
11638
what directive
11639
what directive
11640
dance what
11641
what today
11642
cro who
11643
what book
11644
develop perceptron
11645
wrote person
11646
cities people
11647
wrote steppenwolf
11648
what organization
11649
education country
11650
find information
11651
whay you
11652
what city
11653
what country
11654
what learning
11655
nlp graph
11656
+ 3
11657
get code
11658
what algorithm
11659
load person
11660
welcome child
11661
what name
11662
what planet
11663
person who
11664
distance place
11665
distance place
11666
what kliniken
11667
show images
11668
who person
11669
who person
11670
who person
11671
ask que

12276
person who
12277
repeat name
12278
effects ibuprofen
12279
learn creative
12280
cause damage
12281
who person
12282
tell more
12283
give crow
12284
got it
12285
capital india
12286
preschool place
12287
sing rain
12288
who i
12289
who person
12290
show images
12291
person who
12292
who person
12293
build chatbot
12294
who you
12295
know what
12296
primes primes
12297
sign ramps
12298
won actress
12299
scored goals
12300
scored goals
12301
what name
12302
newspaper india
12303
colours apple
12304
what bike
12305
girl you
12306
want voice
12307
asking question
12308
meaning life
12309
father nation
12310
father nation
12311
father nation
12312
give day
12313
who musicgroup
12314
person who
12315
president states
12316
person who
12317
won cup
12318
what miracles
12319
play sounds
12320
doing what
12321
what name
12322
what bird
12323
what planet
12324
show me
12325
what cake
12326
synonyms support
12327
southside equator
12328
have more
12329
ask question
12330
move hands
12331
pla

12871
know continents
12872
wish me
12873
what lidar
12874
what pi
12875
offering what
12876
get position
12877
have data
12878
what race
12879
hands it
12880
what thing
12881
city nellore
12882
city city
12883
what person
12884
food which
12885
chairman technology
12886
what consonants
12887
sea world
12888
what sea
12889
colours apple
12890
founder tdp
12891
president pakistan
12892
who rademaker
12893
who person
12894
what rock
12895
what type
12896
conductor electrical
12897
state india
12898
elevation airport
12899
like you
12900
give bell
12901
what champion
12902
years person
12903
image elephant
12904
colour rainbow
12905
know what
12906
search image
12907
get city
12908
mode memory
12909
know person
12910
i i
12911
what apple
12912
height mountain
12913
give pineapple
12914
spelling apple
12915
what color
12916
what time
12917
doing what
12918
what date
12919
what field
12920
checking hand
12921
age person
12922
who bros
12923
get city
12924
what currency
12925
had friends
129

give story
13481
feeling book
13482
district up
13483
shutdown computer
13484
show image
13485
country world
13486
give potato
13487
weather pakistan
13488
guest event
13489
set alarm
13490
see flower
13491
discovered telephone
13492
lakh back
13493
who this
13494
what name
13495
images animals
13496
invented thermometer
13497
father who
13498
give capital
13499
thinking what
13500
genius you
13501
know what
13502
person who
13503
name water
13504
move hands
13505
duty he
13506
doing what
13507
religions india
13508
what lien
13509
have brain
13510
help me
13511
capital america
13512
calories apple
13513
what name
13514
spelling apple
13515
do what
13516
president usa
13517
thank you
13518
city country
13519
win cup
13520
had tea
13521
whats name
13522
president india
13523
distance city
13524
distance city
13525
minister india
13526
what name
13527
play rhyme
13528
effects effexor
13529
today day
13530
what name
13531
give shelter
13532
cm place
13533
person who
13534
what train
13535

vec len:  13965
done pickling.!


In [23]:
print(nmod_nn)


[('What is the plot of Titanic?', 'plot', 'Titanic'), ('what is anthem of india?', 'anthem', 'india'), ('birthdate of Person?', 'birthdate', 'Person'), ('founder of tesla car', 'founder', 'car'), ('What is the Language name of a cat', 'name', 'cat'), ('What possible drugs for Dengue Fever?', 'drugs', 'Fever'), ('what is the capital of china', 'capital', 'china'), ('who is the mayor of Place?', 'mayor', 'Place'), ('Is City in Country?', 'City', 'Country'), ('Is Place in Lithuania?', 'Place', 'Lithuania'), ('Is Place in Country?', 'Place', 'Country'), ('What is the capital of the Country?', 'capital', 'Country'), ('What is the total population of Country?', 'population', 'Country'), ('Who are the members of the Pink Floyd?', 'members', 'Floyd'), ('Who are the members of MusicGroup?', 'members', 'MusicGroup'), ('Who are the members of MusicGroup?', 'members', 'MusicGroup'), ('entity information Leaning Tower of Place', 'Tower', 'Place'), ('actors of inception', 'actors', 'inception'), ('W

In [24]:
print(nsubj_nn)


[('Who is Person Church ?', 'Who', 'Church'), ('Who is Person ?', 'Who', 'Person'), ('Who is Person ?', 'Who', 'Person'), ('Who is Person ?', 'Who', 'Person'), ('WHO IS Person?', 'WHO', 'Person'), ('WHO IS MACRON?', 'WHO', 'MACRON'), ("Who is Person'swife？", "'swife？", 'Who'), ('who is Person', 'Person', 'who'), ('What is Organization', 'What', 'Organization'), ('What is Organization', 'What', 'Organization'), ('who is sachin?', 'who', 'sachin'), ('who is sachin?', 'who', 'sachin'), ('what is life', 'what', 'life'), ('what is life', 'what', 'life'), ('what are your drawbacks', 'what', 'drawbacks'), ('Who is Lula?', 'Who', 'Lula'), ('who is Person?', 'who', 'Person'), ('what day is it today', 'today', 'it'), ('who are you', 'who', 'you'), ('Who was Rachmaninov?', 'Who', 'Rachmaninov'), ('who is Person', 'Person', 'who'), ('what is Organization', 'what', 'Organization'), ('Who is Person Kleiner?', 'Who', 'Person'), ('Who is Person Mountain?', 'Who', 'Mountain'), ('What is the German Coun

In [25]:
print(case_nmod)

[("what's on CreativeWork", 'CreativeWork', 'on'), ("what's on CreativeWork", 'CreativeWork', 'on'), ('No of players involved in a cricket match?', 'players', 'of'), ('No of players involved in a football game?', 'players', 'of'), ('and what about Person the emperor', 'Person', 'about'), ('whats new in angular 6', 'angular', 'in'), ('what 10 % of 100', '100', 'of'), ('what about football Country team?', 'team', 'about'), ('Which of these came first? Person, Godzilla or Flash Gordon', 'these', 'of'), ('Which of these came first? Person, Person or Flash Gordon', 'these', 'of'), ('Which of these came first? Person, Person or Person', 'these', 'of'), ("What about Place's weather?", 'weather', 'about'), ('What about wiki mwrkup', 'wiki', 'about'), ('who is the fairest of them all', 'them', 'of'), ('Something about Place', 'Place', 'about'), ('What about Place, England?', 'Place', 'about'), ('and what about luccio?', 'luccio', 'about'), ('Which of these human organ is the heaviest?', 'organ'

In [26]:
print(nmod_prop)

[('Is City in Germany?', 'City', 'Germany'), ('how much bigger is City than mumbai?', 'City', 'mumbai'), ('how much bigger is City than City?', 'City', 'City'), ('How tall is the Statue of Liberty?', 'Statue', 'Liberty'), ('load related Prime Minister of the Country Prime Minister of the Country', 'Minister', 'Minister'), ('president of unitedstats', 'president', 'unitedstats'), ('Where is Statue of Liberty?', 'Statue', 'Liberty'), ('how far is mars from earth', 'mars', 'earth'), ('Who is president of Country', 'president', 'Country'), ('who is the most CreativeWork in the world', 'CreativeWork', 'world'), ("who's the most CreativeWork in the world", 'CreativeWork', 'world'), ('who is the god of war', 'god', 'war'), ('how far is mars from earth', 'mars', 'earth'), ('Kde je Country?', 'Kde', 'Country'), ('who is president of india', 'president', 'india'), ('How far is from AdministrativeArea to LA?', 'AdministrativeArea', 'LA'), ('How far is from AdministrativeArea to City?', 'Administr

In [13]:
print(cop_nn)

[('is lookup online', 'online', 'is'), ('is the earth flat', 'flat', 'is'), ('is the government listening', 'listening', 'is'), ('is the Organization listening', 'listening', 'is'), ('is the earth flat', 'flat', 'is'), ('when is mardi gras', 'gras', 'is'), ('when is mardi gras', 'gras', 'is'), ('when is mardi gras', 'gras', 'is'), ('is the galaxy note eight waterproof', 'waterproof', 'is'), ('is the world flat', 'flat', 'is'), ('is the Organization galaxy note eight waterproof', 'waterproof', 'is'), ('is 3 a prime number', 'number', 'is'), ('is 3 a prime number', 'number', 'is'), ('is paris on a river', 'river', 'is'), ('WHO ist Person', 'Person', 'ist'), ('WHO ist Person', 'Person', 'ist'), ('"hahah" is a laughter', 'laughter', 'is'), ('In which country is City?', 'City', 'is'), ('will be rain tomarow', 'rain', 'be'), ('Are Nazis People?', 'People', 'Are'), ('what is animal', 'animal', 'is'), ('Were is Place', 'Place', 'Were'), ('Was bedeutet Organization?', 'Organization', 'Was'), ('

In [27]:
print(vo)

[('get location City', 'get', 'City'), ('learn more Person Person', 'learn', 'Person'), ('load similar Person Person', 'load', 'Person'), ('get location City', 'get', 'City'), ('learn more Planet Planet', 'learn', 'Planet'), ('load similar Planet Planet', 'load', 'Planet'), ('get location City', 'get', 'City'), ('learn more Person Person', 'learn', 'Person'), ('get location City', 'get', 'City'), ('get location City', 'get', 'City'), ('Who directed MusicGroup of Tomorrow?', 'directed', 'MusicGroup'), ('what you can do?', 'do', 'what'), ('learn more Person Person', 'learn', 'Person'), ('load similar Person Person', 'load', 'Person'), ('who created you', 'created', 'you'), ('How many bones does a cat have?', 'have', 'bones'), ('How to care a newborn?', 'care', 'newborn'), ('Children have disease?', 'have', 'disease'), ('get location City', 'get', 'City'), ('give something about Rachmaninov', 'give', 'something'), ('get location City', 'get', 'City'), ('get location City', 'get', 'City'),